# 02 - Data Cleaning

## Objectives

* Check whether there is duplicate data and if so, address this as necessary
* Remove instances where patients have died from the database, since by definition these patients cannot be readmitted
* Determine the extent of missing data
* Evaluate the most suitable approach to deal with missing data
* Assess column names for inconsistencies and determine how best to handle these
* Clean data

## Inputs

* CSV file generated in previous notebook: outputs/datasets/collection/diabetic_data.csv 

## Outputs

* Cleaned data, to be stored in new folder outputs/datasets/cleaned
* Data cleaning pipeline

---

# Change working directory

* This notebook is stored in the `jupyter_notebooks` subfolder
* The current working directory therefore needs to be changed to the workspace, i.e., the working directory needs to be changed from the current folder to its parent folder

Firstly, the current directory is accessed with os.getcwd()

In [37]:
import os
current_dir = os.getcwd()
current_dir

'c:\\Users\\franc\\diabetes-data-analysis'

Next, the working directory is set as the parent of the current `jupyter_notebooks` directory
* os.path.dirname() gets the parent directory
* os.chir() defines the new current directory
* This allows access to all the files and folders within the workspace, rather than solely those within the `jupyter_notebooks` directory

In [2]:
os.chdir(os.path.dirname(current_dir))
print("You set a new current directory")

You set a new current directory


Finally, it is confirmed that the new current directory has been successfully set

In [3]:
current_dir = os.getcwd()
current_dir

'c:\\Users\\franc\\diabetes-data-analysis'

# Load data

The data is loaded from the outputs/datasets/collection folder:

In [19]:
import pandas as pd
df = pd.read_csv('outputs/datasets/collection/diabetic_data.csv')
df.head()

encounter_id  patient_nbr             race  gender      age weight  \
0       2278392      8222157        Caucasian  Female   [0-10)      ?   
1        149190     55629189        Caucasian  Female  [10-20)      ?   
2         64410     86047875  AfricanAmerican  Female  [20-30)      ?   
3        500364     82442376        Caucasian    Male  [30-40)      ?   
4         16680     42519267        Caucasian    Male  [40-50)      ?   

   admission_type_id  discharge_disposition_id  admission_source_id  \
0                  6                        25                    1   
1                  1                         1                    7   
2                  1                         1                    7   
3                  1                         1                    7   
4                  1                         1                    7   

   time_in_hospital  ... citoglipton insulin  glyburide-metformin  \
0                 1  ...          No      No                   No   
1                 3  ...          No      Up                   No   
2                 2  ...          No      No                   No   
3                 2  ...          No      Up                   No   
4                 1  ...          No  Steady                   No   

   glipizide-metformin  glimepiride-pioglitazone  metformin-rosiglitazone  \
0                   No                        No                       No   
1                   No                        No                       No   
2                   No                        No                       No   
3                   No                        No                       No   
4                   No                        No                       No   

   metformin-pioglitazone  change diabetesMed readmitted  
0                      No      No          No         NO  
1                      No      Ch         Yes        >30  
2                      No      No         Yes         NO  
3                      No      Ch         Yes         NO  
4                      No      Ch         Yes         NO  

[5 rows x 50 columns]

---

# Data Exploration

In order to become more familiar with the dataset, we can create a Pandas profile report:

In [20]:
from pandas_profiling import ProfileReport
pandas_report = ProfileReport(df=df, minimal=True)
pandas_report.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

# Examine data for duplication issues

The first field to check for duplication is `encounter_id`. If the data has been recorded correctly, there should be no duplicate encounters.
* We see from the Pandas profiling report above that there are 100% of distinct values, i.e., there are no duplicates
* This can be checked manually as follows:

In [21]:
df[df.duplicated(subset='encounter_id')]

Empty DataFrame
Columns: [encounter_id, patient_nbr, race, gender, age, weight, admission_type_id, discharge_disposition_id, admission_source_id, time_in_hospital, payer_code, medical_specialty, num_lab_procedures, num_procedures, num_medications, number_outpatient, number_emergency, number_inpatient, diag_1, diag_2, diag_3, number_diagnoses, max_glu_serum, A1Cresult, metformin, repaglinide, nateglinide, chlorpropamide, glimepiride, acetohexamide, glipizide, glyburide, tolbutamide, pioglitazone, rosiglitazone, acarbose, miglitol, troglitazone, tolazamide, examide, citoglipton, insulin, glyburide-metformin, glipizide-metformin, glimepiride-pioglitazone, metformin-rosiglitazone, metformin-pioglitazone, change, diabetesMed, readmitted]
Index: []

[0 rows x 50 columns]

It can be seen that there are no duplicate values recorded for `encounter_id`.

However, there could also be duplicate values for `patient_nbr`, the unique identifier of a patient.
* Since the target variable in the dataset relates to patient readmissions, it seems highly likely that there will be multiple instances of the same patient number within the database
* Looking at the Pandas profiling report above for `patient_nbr`, we see 71,518 distinct values
* We can also look at the duplicated rows:

In [22]:
df[df.duplicated(subset='patient_nbr')]

encounter_id  patient_nbr             race  gender      age weight  \
79           1070256     23043240        Caucasian  Female  [50-60)      ?   
81           1077924     21820806  AfricanAmerican    Male  [50-60)      ?   
143          2309376     41606064        Caucasian    Male  [20-30)      ?   
175          2552952     86240259        Caucasian  Female  [70-80)      ?   
307          3174918      5332491            Other  Female  [60-70)      ?   
...              ...          ...              ...     ...      ...    ...   
101760     443847176     50375628  AfricanAmerican  Female  [60-70)      ?   
101761     443847548    100162476  AfricanAmerican    Male  [70-80)      ?   
101762     443847782     74694222  AfricanAmerican  Female  [80-90)      ?   
101763     443854148     41088789        Caucasian    Male  [70-80)      ?   
101764     443857166     31693671        Caucasian  Female  [80-90)      ?   

        admission_type_id  discharge_disposition_id  admission_source_id  \
79                      2                         1                    4   
81                      1                         6                    7   
143                     2                         1                    2   
175                     1                         3                    7   
307                     6                        25                    7   
...                   ...                       ...                  ...   
101760                  1                         1                    7   
101761                  1                         3                    7   
101762                  1                         4                    5   
101763                  1                         1                    7   
101764                  2                         3                    7   

        time_in_hospital  ... citoglipton insulin  glyburide-metformin  \
79                     3  ...          No  Steady                   No   
81                     3  ...          No      No                   No   
143                    2  ...          No  Steady                   No   
175                   11  ...          No      Up                   No   
307                    5  ...          No  Steady                   No   
...                  ...  ...         ...     ...                  ...   
101760                 6  ...          No    Down                   No   
101761                 3  ...          No    Down                   No   
101762                 5  ...          No  Steady                   No   
101763                 1  ...          No    Down                   No   
101764                10  ...          No      Up                   No   

        glipizide-metformin  glimepiride-pioglitazone  \
79                       No                        No   
81                       No                        No   
143                      No                        No   
175                      No                        No   
307                      No                        No   
...                     ...                       ...   
101760                   No                        No   
101761                   No                        No   
101762                   No                        No   
101763                   No                        No   
101764                   No                        No   

        metformin-rosiglitazone  metformin-pioglitazone  change diabetesMed  \
79                           No                      No      No         Yes   
81                           No                      No      No          No   
143                          No                      No      No         Yes   
175                          No                      No      Ch         Yes   
307                          No                      No      No         Yes   
...                         ...                     ...     ...         ...   
101760                       No

* And confirm the distinct values in a code cell:

In [23]:
print(df['patient_nbr'].nunique())

71518


There is a relatively large number of patients who appear in the database multiple times.
* We see from the above table that there are over 30,000 rows


The obvious question, then, is how these multiple encounters for a single patient should be dealt with.
* To address this question, consider the purpose of the data analysis
* The client wishes to understand the factors that are likely to contribute to readmission, and address these where possible
* In separate encounters, the majority of the variables may vary, such as a patient's time in hospital, medication, and over time even their age and weight, and this may lead to different values for the target variable of readmission
* As such, multiple encounters of a single patient are left in the database for now. This could be revisited at a later stage if necessary

---

# Remove deaths from database

The location to which patients were discharged when they left hospital is included in the database as `discharge_disposition_id`
* A number of patients died
* By definition these patients cannot be readmitted
* While it could also be interesting to look at the pattern of variables relating to death as an outcome, this is not part of the scope of the current analysis
* It therefore makes sense to remove these patients from the database

In [9]:
death_codes = [11, 19, 20, 21]

df = df.loc[~(df['discharge_disposition_id'].isin(death_codes))]
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 100114 entries, 0 to 101765
Data columns (total 50 columns):
 #   Column                    Non-Null Count   Dtype 
---  ------                    --------------   ----- 
 0   encounter_id              100114 non-null  int64 
 1   patient_nbr               100114 non-null  int64 
 2   race                      100114 non-null  object
 3   gender                    100114 non-null  object
 4   age                       100114 non-null  object
 5   weight                    100114 non-null  object
 6   admission_type_id         100114 non-null  int64 
 7   discharge_disposition_id  100114 non-null  int64 
 8   admission_source_id       100114 non-null  int64 
 9   time_in_hospital          100114 non-null  int64 
 10  payer_code                100114 non-null  object
 11  medical_specialty         100114 non-null  object
 12  num_lab_procedures        100114 non-null  int64 
 13  num_procedures            100114 non-null  int64 
 14  num_

---

# Determine the extent of missing data

As seen in the dataframes and the Pandas profiling report above and noted in the previous notebook, there is clearly some missing data.
* The Pandas profiling report is informative but does not tell the full story, since fields recorded as '?' do not show as missing

The next step is to get all variables that have missing values
* An initial approach to this might be to use the `isna` method:

In [10]:
vars_with_missing_data = df.columns[df.isna().any()].tolist()
vars_with_missing_data

['max_glu_serum', 'A1Cresult']

However, it is already clear that `weight`, for example, has missing values, and that these are coded as a question mark `?` in the database.
* Additionally, the client has informed us that non-measurement of max glucose serum and A1C is a potential issue that could have implications for readmission
* As such, a recording of 'None' in the current database does not mean that the data is missing per se, but rather signifies that the value was never recorded in the hospital, a fact that should be taken into account during analysis


Instead, the dataframe can be filtered to show columns that contain a question mark as follows:

In [11]:
vars_with_missing_data = df.columns[df.eq("?").any()].tolist()
vars_with_missing_data

['race',
 'weight',
 'payer_code',
 'medical_specialty',
 'diag_1',
 'diag_2',
 'diag_3']

For columns that contain a question mark, it is useful to know how much of the data is missing
* It is also useful to view this as a percentage, to help determine the most appropriate method of dealing with the missing data

In [12]:
print("Column name; number of datapoints missing; percentage of data missing")
x = 0
while x < len(vars_with_missing_data):
    column_name = vars_with_missing_data[x]
    count = df[column_name].value_counts().get("?", 0)
    print(column_name, count, round(100 * count / len(df[column_name]), 1))
    x += 1
    

Column name; number of datapoints missing; percentage of data missing
race 2239 2.2
weight 96958 96.8
payer_code 39591 39.5
medical_specialty 49129 49.1
diag_1 21 0.0
diag_2 358 0.4
diag_3 1421 1.4


From this it can be seen that there are several columns with missing data. However, the proportion of data that is missing varies widely between columns. Each column is dealt with in turn in the following section.

---

# Handle the missing data appropriately

As noted in the previous section, a number of columns have missing data. Each column must be dealt with separately. Both the extent to which data is missing and the likely utility of the data should be considered.
- The first column with missing data is `race`. The proportion of missing data is low. It is known that race can play an issue in diabetes risk; see, for example, [the CDC's information page on risk factors for diabetes](https://www.cdc.gov/diabetes/basics/risk-factors.html). As such, it seems best to keep the missing data recorded as missing rather than attempting to fill in this column with another value such as the most commonly occurring race in the remainder of the dataset, so that we do not risk causing our model to find a pattern where none in fact exists.
- The second column with missing data is `weight` and the proportion of missing data is large, at 96.8% of the total dataset. Unfortunately, this makes weight unusable as a feature and it will need to be dropped from the dataset.
- `payer_code` and `medical_specialty` both contain a significant proportion of missing data. However, their treatment is different because of the anticipated impact of each of the two features on the target variable of readmission. Our client does not consider that `payer_code` is particularly likely to be relevant to readmission outcomes and as such it can be dropped from the database. However, `medical_specialty` is the code for the specialty of the admitting physician and is considered likely to be highly relevant. For this reason, this variable will be kept and missing values coded as 'missing'.
- The final three columns with missing values are `diag_1`, `diag_2` and `diag_3`. These correspond to the primary, secondary and third diagnosis a patient has received. As such, it is expected that there are some missing values for `diag_2` and `diag_3`; these patients only have one and two diagnoses respectively. The number of missing values for `diag_1` is small and so for these examples the missing data can again be recorded as 'missing'.

Since `encounter_id` and `patient_nbr` have no predictive value, these can also be dropped.

Since the unrecorded values of `max_glu_serum` and `A1Cresult` are currently recorded as 'None', the Pandas profiling report is identifying these as missing. To avoid confusion, these values can be changed to 'Not recorded'.

First, the columns to be removed are dropped. To confirm, the dataframe info is displayed:

In [13]:
df = df.drop(['encounter_id', 'patient_nbr', 'weight', 'payer_code'], axis=1)
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 100114 entries, 0 to 101765
Data columns (total 46 columns):
 #   Column                    Non-Null Count   Dtype 
---  ------                    --------------   ----- 
 0   race                      100114 non-null  object
 1   gender                    100114 non-null  object
 2   age                       100114 non-null  object
 3   admission_type_id         100114 non-null  int64 
 4   discharge_disposition_id  100114 non-null  int64 
 5   admission_source_id       100114 non-null  int64 
 6   time_in_hospital          100114 non-null  int64 
 7   medical_specialty         100114 non-null  object
 8   num_lab_procedures        100114 non-null  int64 
 9   num_procedures            100114 non-null  int64 
 10  num_medications           100114 non-null  int64 
 11  number_outpatient         100114 non-null  int64 
 12  number_emergency          100114 non-null  int64 
 13  number_inpatient          100114 non-null  int64 
 14  diag

The values that need to be updated can then be addressed:

In [14]:
df['max_glu_serum'].fillna('Unrecorded', inplace=True)
df['A1Cresult'].fillna('Unrecorded', inplace=True)
df['race'].replace('?', 'Missing', inplace=True)
df['medical_specialty'].replace('?', 'Missing', inplace=True)
df['diag_1'].replace('?', 'Missing', inplace=True)
df.info()
df.head()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 100114 entries, 0 to 101765
Data columns (total 46 columns):
 #   Column                    Non-Null Count   Dtype 
---  ------                    --------------   ----- 
 0   race                      100114 non-null  object
 1   gender                    100114 non-null  object
 2   age                       100114 non-null  object
 3   admission_type_id         100114 non-null  int64 
 4   discharge_disposition_id  100114 non-null  int64 
 5   admission_source_id       100114 non-null  int64 
 6   time_in_hospital          100114 non-null  int64 
 7   medical_specialty         100114 non-null  object
 8   num_lab_procedures        100114 non-null  int64 
 9   num_procedures            100114 non-null  int64 
 10  num_medications           100114 non-null  int64 
 11  number_outpatient         100114 non-null  int64 
 12  number_emergency          100114 non-null  int64 
 13  number_inpatient          100114 non-null  int64 
 14  diag

race  gender      age  admission_type_id  \
0        Caucasian  Female   [0-10)                  6   
1        Caucasian  Female  [10-20)                  1   
2  AfricanAmerican  Female  [20-30)                  1   
3        Caucasian    Male  [30-40)                  1   
4        Caucasian    Male  [40-50)                  1   

   discharge_disposition_id  admission_source_id  time_in_hospital  \
0                        25                    1                 1   
1                         1                    7                 3   
2                         1                    7                 2   
3                         1                    7                 2   
4                         1                    7                 1   

          medical_specialty  num_lab_procedures  num_procedures  ...  \
0  Pediatrics-Endocrinology                  41               0  ...   
1                   Missing                  59               0  ...   
2                   Missing                  11               5  ...   
3                   Missing                  44               1  ...   
4                   Missing                  51               0  ...   

   citoglipton  insulin  glyburide-metformin  glipizide-metformin  \
0           No       No                   No                   No   
1           No       Up                   No                   No   
2           No       No                   No                   No   
3           No       Up                   No                   No   
4           No   Steady                   No                   No   

  glimepiride-pioglitazone metformin-rosiglitazone metformin-pioglitazone  \
0                       No                      No                     No   
1                       No                      No                     No   
2                       No                      No                     No   
3                       No                      No                     No   
4                       No                      No                     No   

   change diabetesMed readmitted  
0      No          No         NO  
1      Ch         Yes        >30  
2      No         Yes         NO  
3      Ch         Yes         NO  
4      Ch         Yes         NO  

[5 rows x 46 columns]

---

# Assess column names for inconsistencies

The column names should be lowercase, not camelCase, and use underscores between words
* A hyphen will be allowed in the case of a combined medication regimen, for example in the case of `glyburide-metformin` and similar

Firstly, the column names are relisted:

In [15]:
print(df.columns.tolist())

['race', 'gender', 'age', 'admission_type_id', 'discharge_disposition_id', 'admission_source_id', 'time_in_hospital', 'medical_specialty', 'num_lab_procedures', 'num_procedures', 'num_medications', 'number_outpatient', 'number_emergency', 'number_inpatient', 'diag_1', 'diag_2', 'diag_3', 'number_diagnoses', 'max_glu_serum', 'A1Cresult', 'metformin', 'repaglinide', 'nateglinide', 'chlorpropamide', 'glimepiride', 'acetohexamide', 'glipizide', 'glyburide', 'tolbutamide', 'pioglitazone', 'rosiglitazone', 'acarbose', 'miglitol', 'troglitazone', 'tolazamide', 'examide', 'citoglipton', 'insulin', 'glyburide-metformin', 'glipizide-metformin', 'glimepiride-pioglitazone', 'metformin-rosiglitazone', 'metformin-pioglitazone', 'change', 'diabetesMed', 'readmitted']


There are only two columns that do not conform to the quality rules: `A1Cresult` and `diabetesMed`. These can be renamed accordingly:

In [16]:
df.rename(columns = {'A1Cresult':'a1c_result', 'diabetesMed':'diabetes_med'}, inplace = True)
print(df.columns.tolist())

['race', 'gender', 'age', 'admission_type_id', 'discharge_disposition_id', 'admission_source_id', 'time_in_hospital', 'medical_specialty', 'num_lab_procedures', 'num_procedures', 'num_medications', 'number_outpatient', 'number_emergency', 'number_inpatient', 'diag_1', 'diag_2', 'diag_3', 'number_diagnoses', 'max_glu_serum', 'a1c_result', 'metformin', 'repaglinide', 'nateglinide', 'chlorpropamide', 'glimepiride', 'acetohexamide', 'glipizide', 'glyburide', 'tolbutamide', 'pioglitazone', 'rosiglitazone', 'acarbose', 'miglitol', 'troglitazone', 'tolazamide', 'examide', 'citoglipton', 'insulin', 'glyburide-metformin', 'glipizide-metformin', 'glimepiride-pioglitazone', 'metformin-rosiglitazone', 'metformin-pioglitazone', 'change', 'diabetes_med', 'readmitted']


---

# Verify the changes

Repeating the Pandas profile report to confirm, it can also be seen here that the dataset has been updated as desired.

In [17]:
pandas_report = ProfileReport(df=df, minimal=True)
pandas_report.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

---

# Data Cleaning Pipeline

The sections above run through the steps necessary to clean the data in detail and with explanation of the logic and thought process underlying each step that has been incorporated - or deliberately not incorporated - into the data cleaning process.

* However, it is likely to be useful to have all these steps together, so that they are easy to see in one place and can be easily applied to future updated versions of the dataset
* To do this, the steps can be combined into a single pipeline
* The pipeline will have the following steps:
    * Remove deaths
    * Drop columns that are not needed
    * Impute missing data values in columns with missing data that are retained
    * Rename 'None' in `max_glu_serum` and `A1Cresult` as described above
    * Tidy column names where they do not conform to standards

In [49]:
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import FunctionTransformer
from sklearn.compose import ColumnTransformer
from feature_engine.selection import DropFeatures
from feature_engine.imputation import CategoricalImputer

def remove_deaths(X):
      death_codes = [11, 19, 20, 21]
      return X.loc[~(X['discharge_disposition_id'].isin(death_codes))]

def replace_question_mark(X):
    columns_to_replace_question_mark = ['race' , 'medical_specialty']
    X[columns_to_replace_question_mark] = X[columns_to_replace_question_mark].replace('?', 'Missing')
    return X

def rename_columns(X):
    X.rename(columns={'A1Cresult':'a1c_result', 'diabetesMed':'diabetes_med'}, inplace=True)
    return X

data_cleaning_pipeline = Pipeline([
      ('remove_deaths', FunctionTransformer(remove_deaths)),
      ('drop',  DropFeatures(features_to_drop=['encounter_id',
                                    'patient_nbr', 'weight',
                                    'payer_code'])),
      ('replace_question_mark', FunctionTransformer(replace_question_mark)),
      ('categorical',  CategoricalImputer(imputation_method='missing',
                                     fill_value='Unrecorded',
                                     variables=['max_glu_serum' , 'A1Cresult'])),
      ('rename_columns', FunctionTransformer(rename_columns, validate=False)),
])


In [50]:
import pandas as pd
df2 = pd.read_csv('outputs/datasets/collection/diabetic_data.csv')
df2.head()
df2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 101766 entries, 0 to 101765
Data columns (total 50 columns):
 #   Column                    Non-Null Count   Dtype 
---  ------                    --------------   ----- 
 0   encounter_id              101766 non-null  int64 
 1   patient_nbr               101766 non-null  int64 
 2   race                      101766 non-null  object
 3   gender                    101766 non-null  object
 4   age                       101766 non-null  object
 5   weight                    101766 non-null  object
 6   admission_type_id         101766 non-null  int64 
 7   discharge_disposition_id  101766 non-null  int64 
 8   admission_source_id       101766 non-null  int64 
 9   time_in_hospital          101766 non-null  int64 
 10  payer_code                101766 non-null  object
 11  medical_specialty         101766 non-null  object
 12  num_lab_procedures        101766 non-null  int64 
 13  num_procedures            101766 non-null  int64 
 14  num_

In [51]:
df2 = data_cleaning_pipeline.fit_transform(df2)
df2.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 100114 entries, 0 to 101765
Data columns (total 46 columns):
 #   Column                    Non-Null Count   Dtype 
---  ------                    --------------   ----- 
 0   race                      100114 non-null  object
 1   gender                    100114 non-null  object
 2   age                       100114 non-null  object
 3   admission_type_id         100114 non-null  int64 
 4   discharge_disposition_id  100114 non-null  int64 
 5   admission_source_id       100114 non-null  int64 
 6   time_in_hospital          100114 non-null  int64 
 7   medical_specialty         100114 non-null  object
 8   num_lab_procedures        100114 non-null  int64 
 9   num_procedures            100114 non-null  int64 
 10  num_medications           100114 non-null  int64 
 11  number_outpatient         100114 non-null  int64 
 12  number_emergency          100114 non-null  int64 
 13  number_inpatient          100114 non-null  int64 
 14  diag

Verify data cleaning pipeline via Pandas profile report:

In [53]:
pandas_report = ProfileReport(df=df2, minimal=True)
pandas_report.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

---

# Push files to Repo

* In case you don't need to push files to Repo, you may replace this section with "Conclusions and Next Steps" and state your conclusions and next steps.

In [ ]:
import os
try:
  os.makedirs(name='outputs/datasets/cleaned')
except Exception as e:
  print(e)

